# CSE6242 - HW3 - Q1

Pyspark Imports

In [1]:
### DO NOT MODIFY THIS CELL ###
import pyspark
from pyspark.sql import SQLContext
from pyspark.sql.functions import hour, when, col, date_format, to_timestamp, round, coalesce
from pyspark.sql.functions import *

Initialize PySpark Context

In [2]:
### DO NOT MODIFY THIS CELL ###
sc = pyspark.SparkContext(appName="HW3-Q1")
sqlContext = SQLContext(sc)

Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).
23/10/18 14:54:42 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable
23/10/18 14:54:42 WARN Utils: Service 'SparkUI' could not bind on port 4040. Attempting port 4041.
23/10/18 14:54:42 WARN Utils: Service 'SparkUI' could not bind on port 4041. Attempting port 4042.
23/10/18 14:54:42 WARN Utils: Service 'SparkUI' could not bind on port 4042. Attempting port 4043.
23/10/18 14:54:42 WARN Utils: Service 'SparkUI' could not bind on port 4043. Attempting port 4044.
/usr/local/lib/python3.9/dist-packages/pyspark/sql/context.py:113: FutureWarning: Deprecated in 3.0.0. Use SparkSession.builder.getOrCreate() instead.
  warnings.warn(


Define function for loading data

In [3]:
### DO NOT MODIFY THIS CELL ###
def load_data():
    df = sqlContext.read.option("header",True) \
     .csv("yellow_tripdata_2019-01_short.csv")
    return df

### Q1.a

Perform data casting to clean incoming dataset

In [4]:
def clean_data(df):
    '''
    input: df a dataframe
    output: df a dataframe with the all the original columns
    '''
    
    # START YOUR CODE HERE ---------
    from pyspark.sql.types import StructField, StructType, IntegerType, TimestampType, FloatType, StringType

    df = df.withColumn("passenger_count", df["passenger_count"].cast(IntegerType()))
    df = df.withColumn("total_amount", df["total_amount"].cast(FloatType()))
    df = df.withColumn("tip_amount", df["tip_amount"].cast(FloatType()))
    df = df.withColumn("trip_distance", df["trip_distance"].cast(FloatType()))
    df = df.withColumn("fare_amount", df["fare_amount"].cast(FloatType()))
    df = df.withColumn("tpep_pickup_datetime", df["tpep_pickup_datetime"].cast(TimestampType()))
    df = df.withColumn("tpep_dropoff_datetime", df["tpep_dropoff_datetime"].cast(TimestampType()))

    # END YOUR CODE HERE -----------
    
    return df

In [5]:
df = load_data()
df = clean_data(df)
df.select(['passenger_count', 'total_amount', 'tip_amount', 'trip_distance', 'fare_amount', 'tpep_pickup_datetime', 'tpep_pickup_datetime']).printSchema()

root
 |-- passenger_count: integer (nullable = true)
 |-- total_amount: float (nullable = true)
 |-- tip_amount: float (nullable = true)
 |-- trip_distance: float (nullable = true)
 |-- fare_amount: float (nullable = true)
 |-- tpep_pickup_datetime: timestamp (nullable = true)
 |-- tpep_pickup_datetime: timestamp (nullable = true)



### Q1.b

Find rate per person for based on how many passengers travel between pickup and dropoff locations. 

In [6]:
def common_pair(df):
    '''
    input: df a dataframe
    output: df a dataframe with following columns:
            - PULocationID
            - DOLocationID
            - passenger_count
            - per_person_rate
            
    per_person_rate is the total_amount per person for a given pair.
    
    '''
    
    # START YOUR CODE HERE ---------
    from pyspark.sql import Window

    partition_cols = ['PULocationID','DOLocationID']

    group_by_result = df.groupBy(partition_cols).count()
    # group_by_result.show()

    # Filter out any trips that have the same pick-up and drop-off location. 
    df_temp = df.filter((df.PULocationID != df.DOLocationID))
    # group_by_result_difference_location.show()

    # # [4 pts] You will be modifying the function common_pair. 
    # # Return the top 10 pickup-dropoff location pairs that have the highest number of total passengers who have traveled between them. 
    # # Sort the location pairs by total passengers. 
    df_temp = df_temp.withColumn("passenger_count", sum("passenger_count").over(Window.partitionBy(*partition_cols)))
    
    # # For each location pair, also compute 
    #     # the average amount per passenger over all trips (name this per_person_rate), utilizing total_amount.
    df_temp = df_temp.withColumn("total_amount_partition", sum("total_amount").over(Window.partitionBy(*partition_cols)))
    df_temp = df_temp.withColumn("per_person_rate",col("total_amount_partition")/col("passenger_count"))
    
    # # For pairs with the same total passengers, 
    #     # sort them in descending order of per_person_rate.
    # # Rename the column for total passengers to passenger_count. 
    df_temp = df_temp.select(['PULocationID','DOLocationID','passenger_count','per_person_rate']).distinct()
    df_joined  = group_by_result.join(df_temp, partition_cols)
    df_joined = df_joined.orderBy(['passenger_count','per_person_rate'], ascending=False).limit(10)
    df_output = df_joined.drop('count')
    # END YOUR CODE HERE -----------

    return df_output


In [7]:
common_pair(df).show()

+------------+------------+---------------+------------------+
|PULocationID|DOLocationID|passenger_count|   per_person_rate|
+------------+------------+---------------+------------------+
|         246|         162|             30|               0.9|
|         151|         239|             30|0.6666666666666666|
|         107|         181|              3|0.6666666666666666|
|         113|          90|              3|0.6666666666666666|
|         116|          42|              3|0.6666666666666666|
|         138|          50|              3|0.6666666666666666|
|         141|         234|              3|0.6666666666666666|
|         144|         261|              3|0.6666666666666666|
|         161|         170|              3|0.6666666666666666|
|         170|         141|              3|0.6666666666666666|
+------------+------------+---------------+------------------+



### Q1.c

Find trips which trip distances generate the highest tip percentage.

In [8]:
def distance_with_most_tip(df):
    '''
    input: df a dataframe
    output: df a dataframe with following columns:
            - trip_distance
            - tip_percent
            
    trip_percent is the percent of tip out of fare_amount
    
    '''
    
    # START YOUR CODE HERE ---------
    # You will be modifying the function distance_with_most_tip . 
    # Filter the data for trips having fares (fare_amount) 
        # greater than $2.00 and 
        # a trip distance (trip_distance) greater than 0. 
    filtered_df = df.where((df.fare_amount > 2) & (df.trip_distance > 0))
        
    # Calculate the tip percent (tip_amount * 100 / fare_amount) for each trip. 
    # Round all trip distances up to the closest mile and find the average tip_percent for each trip_distance.
    filtered_df = filtered_df.groupBy('trip_distance').agg((mean('tip_amount')*100)/mean('fare_amount'))
    
    # Sort the result in descending order of tip_percent to obtain the top 15 trip distances which tip the most generously. 
    # Rename 
    #   the column for rounded trip distances to trip_distance, and 
    #   the column for average tip percents tip_percent . 
    new_cols = ['trip_distance', 'tip_percent']
    df = filtered_df.toDF(*new_cols) 
    df = df.sort(df.tip_percent.desc()).limit(15)
   

    # END YOUR CODE HERE -----------
    
    return df
distance_with_most_tip(df).show()

+-------------+------------------+
|trip_distance|       tip_percent|
+-------------+------------------+
|          0.7| 30.90909177606756|
|         0.55|30.000000733595627|
|          1.2|28.095238549368723|
|          3.7|27.407407760620117|
|          6.3|26.511627019837846|
|          0.3|26.499998569488525|
|          0.6| 24.54545497894287|
|         1.42|23.999999119685246|
|          2.8|21.666666666666668|
|          8.7|20.724637957586758|
|          1.9|19.047619047619047|
|          2.1|17.000000476837158|
|          1.5| 11.37931018040098|
|         12.3|10.526315789473685|
|          1.3| 8.928571428571429|
+-------------+------------------+



### Q1.d

Determine the average speed at different times of day.

In [9]:
def time_with_most_traffic(df):
    '''
    input: df a dataframe
    output: df a dataframe with following columns:
            - time_of_day
            - am_avg_speed
            - pm_avg_speed
            
    trip_percent is the percent of tip out of fare_amount
    
    '''
    
    # START YOUR CODE HERE ---------
    from pyspark.sql.functions import dayofweek,date_format, unix_timestamp,format_number
    from pyspark.sql.types import DecimalType
    from pyspark.sql import Window
    
    # You will be modifying the function time_with_most_traffic to determine which hour of the day has the most traffic. 
    
    df = df.withColumn('time_of_day',date_format(col("tpep_pickup_datetime"),"K"))
    df = df.withColumn('AM_PM',date_format(col("tpep_pickup_datetime"),"a"))
    df = df.withColumn('diff_in_seconds',col("tpep_dropoff_datetime").cast("long") - col('tpep_pickup_datetime').cast("long"))

    partition_cols = ['time_of_day','AM_PM']
    
    # Calculate the traffic for a particular hour using the average speed of all taxi trips which began during that hour. 
    # Calculate the average speed as the average trip_distance divided by the average trip time, as distance per hour.
    group_by_result = df.groupBy(partition_cols).count()
    
    df  = group_by_result.join(df, partition_cols)
    
    df = df.withColumn("trip_distance_sum", sum("trip_distance").over(Window.partitionBy(*partition_cols)))
    df = df.withColumn("average_trip_distance",col("trip_distance_sum")/col("count"))

    df = df.withColumn("trip_time_sum_s", sum("diff_in_seconds").over(Window.partitionBy(*partition_cols)))
    df = df.withColumn("average_trip_time_s",col("trip_time_sum_s")/col("count"))

    df = df.withColumn("average_speed",col("average_trip_distance")/col("average_trip_time_s"))

    df = df.select(['time_of_day','AM_PM','average_speed']).distinct()
    df  = group_by_result.join(df, partition_cols)
    
    # A day with low average speed indicates high levels of traffic. 
    # The average speed may be 0, indicating very high levels of traffic.

    # Additionally, you must separate the hours into AM and PM, with hours 0:00-11:59 being AM, and hours 12:00-23:59 being PM. 
    # Convert these times to the 12 hour time, so you can match the below output. 
    # For example, 
      # the row with 1 as time of day, 
        # should show the average speed between 1 am and 2 am in the am_avg_speed column, 
        # and between 1 pm and 2pm in the pm_avg_speed column.

    # Use date_format along with the appropriate pattern letters to format the time of day so that it matches the example output below. 
    
    # Your final table should 
      # contain values sorted from 0-11 for time_of_day. 
      # There may be data missing for a time of day, and it may be null for am_avg_speed or pm_avg_speed. 
      # If an hour has no data for am or pm, there may be missing rows. 
        # Do not include any additional rows for times of day which are not represented in the data. 

    df = df.select(['time_of_day','AM_PM','average_speed']).limit(15)
    
    from pyspark.sql import SparkSession
    spark = SparkSession.builder.getOrCreate()

    time_data = [
        [0,None,None],
        [1,None,None],
        [2,None,None],
        [3,None,None],
        [4,None,None],
        [5,None,None],
        [6,None,None],
        [7,None,None],
        [8,None,None],
        [9,None,None],
        [10,None,None],
        [11,None,None]
    ]
                                  
    for i in range(0,len(time_data)):
        time_int_wanted = time_data[i][0]
    
        for j in range(0, len(df.collect())):
            time_int = df.collect()[j][0]
            AM_PM = df.collect()[j][1]
            average_speed = df.collect()[j][2]

            if (time_int == str(time_int_wanted)):
                if (AM_PM =="AM"):
                    time_data[int(time_int)][1] = float(average_speed)
                if (AM_PM =="PM"):
                    time_data[int(time_int)][2] = float(average_speed)

    df_output = spark.createDataFrame(data=time_data, schema=["time_of_day","am_avg_speed","pm_avg_speed"])
    # END YOUR CODE HERE -----------
    
    return df_output

time_with_most_traffic(df).show()

PySparkValueError: [CANNOT_DETERMINE_TYPE] Some of types cannot be determined after inferring.

### The below cells are for you to investigate your solutions and will not be graded
## Ensure they are commented out prior to submitting to Gradescope to avoid errors

In [ ]:
# df = load_data()
# df = clean_data(df)

In [ ]:
# common_pair(df).show()

In [ ]:
# distance_with_most_tip(df).show()

In [ ]:
# time_with_most_traffic(df).show()